In [41]:
from datasets import load_dataset, concatenate_datasets


In [70]:
cv = load_dataset("mozilla-foundation/common_voice_8_0", "mr", split="train+validation", use_auth_token=True)
print(cv)
openslr = load_dataset("openslr", "SLR64", split="train")
print(openslr)
samanantar = load_dataset("shivam/marathi_samanantar_processed", split="train")
print(samanantar)
pib = load_dataset("shivam/marathi_pib_processed", split="train")
print(pib)
opus = load_dataset("opus100", "en-mr", split="train").map(lambda example: {"sentence": example["translation"]["mr"]})
print(opus)
tatoeba = load_dataset("tatoeba", "en-mr", split="train").map(lambda example: {"sentence": example["translation"]["mr"]})
print(tatoeba)
tapaco = load_dataset("tapaco", "mr", split="train")
print(tapaco)



Reusing dataset common_voice (/home/ubuntu/.cache/huggingface/datasets/mozilla-foundation___common_voice/mr/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


Dataset({
    features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
    num_rows: 698
})


Reusing dataset open_slr (/home/ubuntu/.cache/huggingface/datasets/open_slr/SLR64/0.0.0/e0fb9e36094eff565efe812d1aba158f6a46ce834cb9705c91d1e2d6ba78ed31)


Dataset({
    features: ['path', 'audio', 'sentence'],
    num_rows: 1569
})


Using custom data configuration shivam--marathi_samanantar_processed-538aa7995793bd87
Reusing dataset parquet (/home/ubuntu/.cache/huggingface/datasets/parquet/shivam--marathi_samanantar_processed-538aa7995793bd87/0.0.0/0b6d5799bb726b24ad7fc7be720c170d8e497f575d02d47537de9a5bac074901)


...

Reusing dataset tatoeba (/home/ubuntu/.cache/huggingface/datasets/tatoeba/en-mr/2021.7.22/b3ea9c6bb2af47699c5fc0a155643f5a0da287c7095ea14824ee0a8afd74daf6)


  0%|          | 0/53462 [00:00<?, ?ex/s]

Dataset({
    features: ['id', 'translation', 'sentence'],
    num_rows: 53462
})


Reusing dataset tapaco (/home/ubuntu/.cache/huggingface/datasets/tapaco/mr/1.0.0/71d200534b520a174927a8f0479c06220a0a6fb5201a84ebfce19006c6354698)


Dataset({
    features: ['paraphrase_set_id', 'sentence_id', 'paraphrase', 'lists', 'tags', 'language'],
    num_rows: 16413
})


In [71]:
cv = cv.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes", 'path', 'audio'])
openslr = openslr.remove_columns(['path', 'audio'])
samanantar = samanantar.rename_column("text","sentence")
pib = pib.rename_column("text","sentence")
opus = opus.remove_columns(["translation"])
tatoeba = tatoeba.remove_columns(['id','translation'])
tapaco = tapaco.remove_columns(['paraphrase_set_id', 'sentence_id', 'lists', 'tags', 'language']).rename_column("paraphrase","sentence")

text_dataset = concatenate_datasets([cv, openslr, samanantar, pib, opus, tatoeba, tapaco])
text_dataset


Dataset({
    features: ['sentence'],
    num_rows: 3263574
})

In [73]:
chars_to_ignore_regex = '[,?.!\-\;\:"“%‘”�—’…–\।\!\"\,\-\.\?\:\|\“\”\–\;\'\’\‘\॔]'   # change to the ignored characters of your fine-tuned model

In [74]:
import re

def extract_text(batch):
    text = batch["sentence"]
    batch["text"] = re.sub(chars_to_ignore_regex, "", text.lower())
    return batch

In [76]:
dataset = text_dataset.map(extract_text, remove_columns=text_dataset.column_names)
dataset

  0%|          | 0/3263574 [00:00<?, ?ex/s]

Dataset({
    features: ['text'],
    num_rows: 3263574
})

In [77]:
dataset[0]

{'text': 'शिवाय त्यांना कवितेचा आणि चित्रकलेचा छंद होता'}

In [78]:
with open("text.txt", "w") as file:
    file.write(" ".join(dataset["text"]))

In [82]:
!kenlm/build/bin/lmplz -o 5 <"text.txt" > "5gram.arpa"

=== 1/5 Counting and sorting n-grams ===
Reading /ebs/learn/ASR/text.txt
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
Unigram tokens 29706056 types 776336
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:9316032 2:20102516736 3:37692219392 4:60307550208 5:87948517376
Statistics:
1 776335 D1=0.705463 D2=1.0456 D3+=1.33671
2 8433103 D1=0.790673 D2=1.11187 D3+=1.35296
3 18421039 D1=0.878727 D2=1.22916 D3+=1.39519
4 24029132 D1=0.935948 D2=1.36969 D3+=1.49375
5 26433229 D1=0.885046 D2=1.58244 D3+=2.0281
Memory estimate for binary LM:
type      MB
probing 1637 assuming -p 1.5
probing 1931 assuming -r models -p 1.5
trie     833 without quantization
trie     476 assuming -q 8 -b 8 quantization 
trie     726 assuming -a 22 array pointer compression
trie     368 assuming -a 22 -q 8 -b 8 array pointer compression and quanti

In [83]:
!head -20 5gram.arpa

\data\
ngram 1=776335
ngram 2=8433103
ngram 3=18421039
ngram 4=24029132
ngram 5=26433229

\1-grams:
-6.9649706	<unk>	0
0	<s>	-0.10200334
-3.8677218	शिवाय	-0.29601222
-3.0139472	त्यांना	-0.54708624
-5.7931695	कवितेचा	-0.10200334
-2.2375891	आणि	-0.5685015
-6.046465	चित्रकलेचा	-0.16192785
-4.874536	छंद	-0.3758324
-3.150044	होता	-0.53179973
-6.514799	पारंपरिकदृष्ट्या	-0.10200334
-4.837577	ज्वारी	-0.3880814
-4.9689674	बाजरी	-0.32780117


In [85]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
    has_added_eos = False
    for line in read_file:
        if not has_added_eos and "ngram 1=" in line:
            count=line.strip().split("=")[-1]
            write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
        elif not has_added_eos and "<s>" in line:
            write_file.write(line)
            write_file.write(line.replace("<s>", "</s>"))
            has_added_eos = True
        else:
            write_file.write(line)

In [86]:
!head -20 5gram_correct.arpa

\data\
ngram 1=776336
ngram 2=8433103
ngram 3=18421039
ngram 4=24029132
ngram 5=26433229

\1-grams:
-6.9649706	<unk>	0
0	<s>	-0.10200334
0	</s>	-0.10200334
-3.8677218	शिवाय	-0.29601222
-3.0139472	त्यांना	-0.54708624
-5.7931695	कवितेचा	-0.10200334
-2.2375891	आणि	-0.5685015
-6.046465	चित्रकलेचा	-0.16192785
-4.874536	छंद	-0.3758324
-3.150044	होता	-0.53179973
-6.514799	पारंपरिकदृष्ट्या	-0.10200334
-4.837577	ज्वारी	-0.3880814


In [87]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("smangrul/xls-r-300m-mr")

In [88]:
vocab_dict = processor.tokenizer.get_vocab()
sorted_vocab_dict = {k.lower(): v for k, v in sorted(vocab_dict.items(), key=lambda item: item[1])}
sorted_vocab_dict


{'|': 0,
 'ँ': 1,
 'ं': 2,
 'ः': 3,
 'अ': 4,
 'आ': 5,
 'इ': 6,
 'ई': 7,
 'उ': 8,
 'ऊ': 9,
 'ऋ': 10,
 'ए': 11,
 'ऐ': 12,
 'ऑ': 13,
 'ओ': 14,
 'औ': 15,
 'क': 16,
 'ख': 17,
 'ग': 18,
 'घ': 19,
 'च': 20,
 'छ': 21,
 'ज': 22,
 'झ': 23,
 'ञ': 24,
 'ट': 25,
 'ठ': 26,
 'ड': 27,
 'ढ': 28,
 'ण': 29,
 'त': 30,
 'थ': 31,
 'द': 32,
 'ध': 33,
 'न': 34,
 'प': 35,
 'फ': 36,
 'ब': 37,
 'भ': 38,
 'म': 39,
 'य': 40,
 'र': 41,
 'ऱ': 42,
 'ल': 43,
 'ळ': 44,
 'व': 45,
 'श': 46,
 'ष': 47,
 'स': 48,
 'ह': 49,
 '़': 50,
 'ा': 51,
 'ि': 52,
 'ी': 53,
 'ु': 54,
 'ू': 55,
 'ृ': 56,
 'ॄ': 57,
 'ॅ': 58,
 'े': 59,
 'ै': 60,
 'ॉ': 61,
 'ॊ': 62,
 'ो': 63,
 'ौ': 64,
 '्': 65,
 'ॲ': 66,
 '[unk]': 67,
 '[pad]': 68,
 '<s>': 69,
 '</s>': 70}

In [89]:
from pyctcdecode import build_ctcdecoder

decoder = build_ctcdecoder(
    labels=list(sorted_vocab_dict.keys()),
    kenlm_model_path="5gram_correct.arpa",
)

Loading the LM will be faster if you build a binary file.
Reading /ebs/learn/ASR/5gram_correct.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
Found entries of length > 1 in alphabet. This is unusual unless style is BPE, but the alphabet was not recognized as BPE type. Is this correct?
Unigrams and labels don't seem to agree.


In [90]:
decoder

In [91]:
from transformers import Wav2Vec2ProcessorWithLM

processor_with_lm = Wav2Vec2ProcessorWithLM(
    feature_extractor=processor.feature_extractor,
    tokenizer=processor.tokenizer,
    decoder=decoder
)

In [92]:
processor_with_lm.save_pretrained("./smangrul/xls-r-300m-mr/")

In [95]:
processor_with_lm.save_pretrained("./../xls-r-300m-mr-model/")